In [6]:
#This Jupyter Notebook file contains python code which allows to generate the Hamiltonian input files for the mVMC c mVMC code  (https://github.com/issp-center-dev/mVMC) For the NxN honeycomb lattice (2xNxN lattice sites), assuming:
#-Arbitrary chosen range of hoppings
#-Arbitrary chosen range of density-density Coulomb interactions
#-Arbitrary chosen range of exchange/Hund/pairhopp interaction terms
#-Arbitrary chosen range of correlated hopping interaction terms

import numpy as np

In [7]:
L=70 #dimension of unit cell for the triangular lattice it can be any number > 0

v_x=np.array([L,0])
v_y=np.array([L/2,L*np.sqrt(3)/2])

w_x=[L/2,L*np.sqrt(3)/6]
w_y=[L,L*np.sqrt(3)/3]



def get_distance(i,j,orb1,orb2,L=70):
    R=i*v_x+j*v_y
    if(orb1==0):
        R=R-(v_x/3+v_y/3)
    if(orb1==1):
        R=R-(2*v_x/3+2*v_y/3)
    if(orb2==0):
        R=R+v_x/3+v_y/3
    if(orb2==1):
        R=R+2*v_x/3+2*v_y/3
    d=R[0]**2+R[1]**2
    return d,i,j,orb1,orb2

In [8]:
class Hopping:
    def __init__(self, i= 0, j = 0, s1=0, s2=0, amplitude = -1):
            self.i = i
            self.j = j            
            self.s1 = s1
            self.s2 = s2
            self.amplitude=amplitude
    def __str__(self):
         return str(self.i)+" "+str(self.s1)+" "+str(self.j)+" "+str(self.s2)+ " " + str(self.amplitude)
    def __repr__(self):
          return self.__str__()

In [9]:
def get_n(nindex=0,ax=0,ay=0,Lx=L,Ly=L,amplitude= -1.0):
    nlist=[]
    R=Lx+Ly
    for i in range(-R,R+1):
        for j in range(-R,R+1):
            out=get_distance(i,j,0,0,L)
            nlist.append(out)
            out=get_distance(i,j,1,0,L)
            
            nlist.append(out)
            out=get_distance(i,j,1,1,L)
            nlist.append(out)
            out=get_distance(i,j,0,1,L)
            nlist.append(out)
    llist=list(nlist)
    llist.sort()
    
    idxs = []
    idxs.append(0)
    d=0.0
    for i in range(0,len(llist)-1):
           if llist[i][0] > llist[i-1][0]+1:
                idxs.append(i-1)
               
    start = idxs[nindex]+1
    end = idxs[nindex+1]+1
    if nindex==0:
        start=0
        end=2
   
    lx = 0
    ly = 0
    hoppings=[]
    for i in range(start,end):
       
        lx = llist[i][1]+ax
        ly = llist[i][2]+ay
        
        if lx < 0:
                lx=Lx+lx
        if lx >= Lx:
                lx=lx-Lx 
    
        if ly < 0:
                ly=Ly+ly
        if ly >= Ly:
                ly=ly-Ly
        
        id1 = (ax+ay*Lx)*2+llist[i][3]
        id2 = (lx+ly*Lx)*2+llist[i][4]
        
    
        hoppings.append(Hopping(id1,id2,0,0,amplitude))
        hoppings.append(Hopping(id1,id2,1,1,amplitude))
       
    return hoppings
    
def get_n_c(nindex=0,ax=0,ay=0,Lx=2,Ly=2,amplitude= -1.0):
    nlist=[]
    R=Lx+Ly
    for i in range(-R,R+1):
        for j in range(-R,R+1):
            out=get_distance(i,j,0,0,L)
            nlist.append(out)
            out=get_distance(i,j,1,0,L)
            
            nlist.append(out)
            out=get_distance(i,j,1,1,L)
            nlist.append(out)
            out=get_distance(i,j,0,1,L)
            nlist.append(out)
    llist=list(nlist)
    llist.sort()
    idxs = []
    idxs.append(0)
    d=0.0
    for i in range(0,len(llist)-1):
           if llist[i][0] > llist[i-1][0]+1:
                idxs.append(i-1)
                 
 
    
    
    
    start = idxs[nindex]+1
    end = idxs[nindex+1]+1
    if nindex==0:
        start=0
        end=2
   
    lx = 0
    ly = 0
    hoppings=[]
    for i in range(start,end):
        #print (lx,ly)
        lx = llist[i][1]+ax
        ly = llist[i][2]+ay
        
        if lx < 0:
                lx=Lx+lx
        if lx >= Lx:
                lx=lx-Lx 
    
        if ly < 0:
                ly=Ly+ly
        if ly >= Ly:
                ly=ly-Ly
        
        id1 = (ax+ay*Lx)*2+llist[i][3]
        id2 = (lx+ly*Lx)*2+llist[i][4]
        
    
        hoppings.append(Hopping(id1,id2,0,0,amplitude))
        
        
    return hoppings
       
 

In [10]:
#Set system size:
Lp =12 #244 sites

In [ ]:
#single particle (kinetic) part of Hamiltonian

In [ ]:
#amplitudes - index zero refers to on-site, index 1 to the nearest neighbor etc..
amplitudes = [1,2,3,4,5]


#print(get_n(ax=0,ay=0,nindex=1,Lx=4,Ly=4))
hoppings=[]
for i in range(0,len(amplitudes)):
    for ax in range(0,Lp):
        for ay in range(0,Lp):
            output=get_n(ax=ax,ay=ay,nindex=i,amplitude=-amplitudes[i],Lx=Lp,Ly=Lp)
            for j in range(0,len(output)):
                hoppings.append(output[j])
            

N=len(hoppings)
f=open("trans.def","w")
#mVMC preambule
f.write("========================\n")
f.write("%s %s\n" % ("NTransfer   ",N))
f.write("========================\n")
f.write("========i_j_s_tijs======\n") 
f.write("========================\n")
for item in hoppings:
        f.write("%s\n" % (item))
f.close()

In [ ]:
#Hubbard (on-site) interactions
amplitudes=[4]

f=open("coulombintra.def","w")
#f.write("=============================================\n")
f.write("========================\n")
f.write("%s %s\n" % ("NCoulombIntra     ",2*Lp**2))
f.write("========================\n")
f.write("========CoulombIntra======\n") 
f.write("========================\n")
for i in range(0,2*Lp**2):
        f.write("%s %s\n" % (i,amplitudes[0]))
f.close()

In [ ]:
#V_{i,j} density-density coulomb interactions, the same indexing as for hoppings
amplitudes=[1,2,3,4]
hoppings=[]
for i in range(0,len(amplitudes)):
    for ax in range(0,Lp):
        for ay in range(0,Lp):
            output=get_n_c(ax=ax,ay=ay,nindex=i,amplitude=amplitudes[i],Lx=Lp,Ly=Lp)
            for j in range(0,len(output)):
                hoppings.append(output[j])
            


f=open("coulombinter.def","w")

inters=[]
for item in hoppings:
    if item.i < item.j:
        inters.append([item.i,item.j,item.amplitude])
N=len(inters)
#mVMC preambule
f.write("========================\n")
f.write("%s %s\n" % ("NCoulombInter   ",N))
f.write("========================\n")
f.write("========CoulombInter======\n") 
f.write("========================\n")
for item in inters:
        f.write("%s %s %s\n" % (item[0],item[1],item[2]))



f.close()

In [ ]:
#JHUND_{i,j} Hund interactions, the same indexing as for hoppings
amplitudes=[1,2,3,4]
hoppings=[]
for i in range(1,len(amplitudes)):
    for ax in range(0,Lp):
        for ay in range(0,Lp):
            output=get_n_c(ax=ax,ay=ay,nindex=i,amplitude=amplitudes[i],Lx=Lp,Ly=Lp)
            for j in range(0,len(output)):
                hoppings.append(output[j])
            


f=open("hund.def","w")

inters=[]
for item in hoppings:
    if item.i < item.j:
        inters.append([item.i,item.j,item.amplitude])
N=len(inters)
#mVMC preambule
f.write("========================\n")
f.write("%s %s\n" % ("NHund   ",N))
f.write("========================\n")
f.write("========Hund======\n") 
f.write("========================\n")
for item in inters:
        f.write("%s %s %s\n" % (item[0],item[1],item[2]))
f.close()

In [ ]:
#JP_{i,j} pair-hopping interactions, the same indexing as for hoppings
amplitudes=[1,2,3,4]
hoppings=[]
for i in range(1,len(amplitudes)):
    for ax in range(0,Lp):
        for ay in range(0,Lp):
            output=get_n_c(ax=ax,ay=ay,nindex=i,amplitude=amplitudes[i],Lx=Lp,Ly=Lp)
            for j in range(0,len(output)):
                hoppings.append(output[j])
            


f=open("pair.def","w")

inters=[]
for item in hoppings:
    if item.i < item.j:
        inters.append([item.i,item.j,item.amplitude])
N=len(inters)
f.write("========================\n")
f.write("%s %s\n" % ("NPairHop   ",N))
f.write("========================\n")
f.write("========Pair======\n") 
f.write("========================\n")
for item in inters:
        f.write("%s %s %s\n" % (item[0],item[1],item[2]))



f.close()

In [ ]:
#JEX_{i,j} exchange interactions, the same indexing as for hoppings
amplitudes=[1,2,3,4]
hoppings=[]
for i in range(1,len(amplitudes)):
    for ax in range(0,Lp):
        for ay in range(0,Lp):
            output=get_n_c(ax=ax,ay=ay,nindex=i,amplitude=amplitudes[i],Lx=Lp,Ly=Lp)
            for j in range(0,len(output)):
                hoppings.append(output[j])
            


f=open("exchange.def","w")

inters=[]
for item in hoppings:
    if item.i < item.j:
        inters.append([item.i,item.j,item.amplitude])
N=len(inters)
f.write("========================\n")
f.write("%s %s\n" % ("NExchange   ",N))
f.write("========================\n")
f.write("========Exchange======\n") 
f.write("========================\n")
for item in inters:
        f.write("%s %s %s\n" % (item[0],item[1],item[2]))



f.close()

In [ ]:
#VC_{i,j} correlated hopping interactions, the same indexing as for hoppings
amplitudes=[1,2,3,4]
hoppings=[]
for i in range(1,len(amplitudes)):
    for ax in range(0,Lp):
        for ay in range(0,Lp):
            output=get_n_c(ax=ax,ay=ay,nindex=i,amplitude=amplitudes[i],Lx=Lp,Ly=Lp)
            for j in range(0,len(output)):
                hoppings.append(output[j])
            


f=open("correlatedh.def","w")

inters=[]
for item in hoppings:
    if item.i != item.j:
        inters.append([item.i,item.j,item.amplitude])
N=len(inters)
f.write("========================\n")
f.write("%s %s\n" % ("NInterAll   ",N*16))
f.write("========================\n")
f.write("========zInterAll======\n") 
f.write("========================\n")
for item in inters:
    for spin1 in range(0,2):
        for spin2 in range(0,2):
            f.write("%s %s %s %s %s %s %s %s %s\n" % (item[0],spin1,item[1],spin1,item[1],spin2,item[1],spin2,0.5*item[2]))
            f.write("%s %s %s %s %s %s %s %s %s\n" % (item[1],spin1,item[1],spin1,item[0],spin2,item[1],spin2,0.5*item[2]))
            f.write("%s %s %s %s %s %s %s %s %s\n" % (item[1],spin1,item[1],spin1,item[1],spin2,item[0],spin2,0.5*item[2]))
            f.write("%s %s %s %s %s %s %s %s %s\n" % (item[1],spin1,item[0],spin1,item[1],spin2,item[1],spin2,0.5*item[2]))


f.close()